### Imports

In [1]:
'''



'''
pass

In [2]:
'''
Take attractor out of generative output

'''

import os
import sys
import numpy as np
import json 
import math
import random
import time
import copy
from datetime import datetime

import torch
from torch import nn
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader
from torch.utils.data.sampler import Sampler

import plotly as py
import plotly.offline as offline
import plotly.graph_objs as go
import plotly.figure_factory as ff
import plotly.io as pio

layout = go.Layout(
    height = 800,
    width = 800,
    hovermode= 'closest',
    showlegend=True,
)

CURRENT_MODEL_SAVE_DIR = './save/'
offline.init_notebook_mode(connected=True)
np.set_printoptions(precision=5, suppress=True)
print(f'pytorch={torch.__version__}, cuda={torch.version.cuda}, numpy={np.__version__}, python={sys.version}')
torch.cuda.is_available()

pytorch=1.8.0, cuda=10.2, numpy=1.19.2, python=3.8.5 (default, Sep  3 2020, 21:29:08) [MSC v.1916 64 bit (AMD64)]


True

### Code

In [3]:
def exists(val):
    return val is not None

#activation
class Snake(nn.Module):
    def __init__(self, alpha):
        super().__init__()
        self.a = alpha
        
    def forward(self, x):
        return x + ((torch.sin(self.a* x)) ** 2) /self.a
    
class Model(nn.Module):
    def __init__(self, input_size, hidden_size, output_size, activation):
        super(Model, self).__init__()

        # Defining some parameters
        self.input_size = input_size
        self.hidden_size = hidden_size
        self.activation = activation

        #Defining the layers
        # RNN Layer
        self.rnn = RNN(input_size, hidden_size, output_size, activation)   
        # Fully connected linear layer
        self.fc = nn.Linear(hidden_size, output_size)
    
    def forward(self, x, hidden=None):       
        #Initializing hidden state for first input using method defined below
        if hidden is None:
            hidden = self.init_hidden(x.shape[0])

        # Passing in the input and hidden state into the model and obtaining outputs
        out, hidden = self.rnn(x, hidden)
        
        # Reshaping the outputs such that it can be fit into the fully connected layer
        out = out.contiguous().view(-1, self.hidden_size)
        out = self.fc(out)
        
        return out, hidden
    
    def init_hidden(self, input_size):
        # This method generates the first hidden state of zeros which we'll use in the forward pass
        hidden = torch.zeros(input_size, self.hidden_size).to(device)
         # We'll send the tensor holding the hidden state to the device we specified earlier as well
        return hidden
    
class RNN(nn.Module):
    # you can also accept arguments in your model constructor
    def __init__(self, data_size, hidden_size, output_size, activation):
        super(RNN, self).__init__()
        self.activation = activation
        self.hidden_size = hidden_size
        input_size = data_size + hidden_size

        self.i2h0 = nn.Linear(input_size, hidden_size)
        self.h2o0 = nn.Linear(hidden_size, output_size)
        self.i2h1 = nn.Linear(hidden_size+output_size, hidden_size)
        self.h2o1 = nn.Linear(hidden_size, output_size)

    def forward(self, data, last_hidden):
        input = torch.cat((data, last_hidden), 1)
        hidden = self.i2h0(input)
        hidden = self.activation(hidden)
        output = self.h2o0(hidden)
        output = self.activation(output)
#         print(f'1 {input.shape}{hidden.shape}{output.shape}')
        
        input = torch.cat((output, hidden), 1)
#         print(f'2 {input.shape}{hidden.shape}{output.shape}')
        hidden = self.i2h1(input)
        hidden = self.activation(hidden)
        output = self.h2o1(hidden)
        output = self.activation(output)

        return hidden, output 

class Pair_Model(nn.Module):
    def __init__(self, inputModel, outputModel):
        super(Pair_Model, self).__init__()  # just run the init of parent class (nn.Module)        
        self.inputModel = inputModel
        self.outputModel = outputModel
        
    def forward(self, x):
        x, h = self.inputModel(x)
        x, h = self.outputModel(x)       
        return x, h

In [4]:
class Char_Dataset:
    def __init__(self, char_data, parms={}):
        '''
        Dataset creates a set of harmonic (multi-hand clocks)
        the output can be rotated a number of steps tp crate a dynamic system
        randomness can be added to the input to create an attractor to the output
        
        '''
        if parms=={} :
            self.x_input_a = None
            self.x_target_a = None

            self.x_input = None
            self.x_target = None
            
            return #return empty class (i.e. to be populated by dataset_range)

        #populate class variables 
        self.notes = []
        self.parms = parms
        loop_obs = parms['loop_obs']
        cycle_counts = parms['cycle_counts']
        in_radius = parms['in_radius']
        center = parms['center']
        step_offset = parms['step_offset']
        skip_loops = parms['skip_loops']
                
        if in_radius==[]:
            in_radius = [.5, np.random.rand()*.5+.3]
        x_input_a,x_target_a = multi_radius_inputs_outputs(loop_obs, cycle_counts, in_radius, 
                                center, step_offset,skip_loops)
        
        num_attractor = len(in_radius)
        char_target_a = np.vstack([char_data]*num_attractor) #duplicate across attractors

        self.x_input_a = x_input_a 
        self.x_target_a = x_target_a       
        self.x_filter_a = x_target_a[:]       
        self.char_target_a = char_target_a
        self.char_filter_a = char_target_a[:]
        
        self.x_input = torch.tensor(self.x_input_a, dtype=torch.float)
        self.x_target = torch.tensor(self.x_target_a, dtype=torch.float)
        self.char_target = torch.tensor(self.char_target_a, dtype=torch.float)
        
        self.x_filter = torch.tensor(self.x_filter_a, dtype=torch.float)
        self.char_filter = torch.tensor(self.char_filter_a, dtype=torch.float)

    def __getitem__(self, idx):
        return self.x_filter[idx], self.char_filter[idx]

    def __len__(self):
        return len(self.x_filter)


In [5]:
def multi_radius_inputs_outputs2D(loop_obs=10,in_radius=[.4, .5], target_radius_delta=0.3,radius_range_offset=.3, step_offset=1,center=.5):

    inList=[]
    targetList=[]
    angles = np.linspace(0, 2*math.pi, loop_obs+1)[:-1] #remove overlap start/finish
    for radius in in_radius:
        target_radius = target_radius_delta*(.5-radius)+radius

        cd_in  = get_circle_data(loop_obs, radius)
        cd_target  = get_circle_data(loop_obs, target_radius)
        cd_target = get_circle_offset(cd_target,step_offset)
        
        inList.append(cd_in)
        targetList.append(cd_target)
        
    return np.array(inList), np.array(targetList)

def get_circle_data(loop_obs=30, radius=.5, center=[.5,.5]):
    a = np.linspace(0,1,loop_obs+1)*2*math.pi
    a = np.dstack([np.sin(a),np.cos(a)])[0]
    return (radius*a+center)[:-1]

def get_circle_offset(circle,step_offset=0):
    return np.concatenate([circle[step_offset:],circle[:step_offset]])

def multi_radius_inputs_outputs(loop_obs, cycle_counts,  in_radius,
                                center,step_offset,skip_loops):
    '''
    '''    
    #calc cumulative cycles
    cycles = [1] #initialize first cycle (should be one for unity across all cycles)
    for i, n in enumerate(cycle_counts[1:]):
        cycles.append(cycles[i]*n)
    total_obs = cycles[-1]*loop_obs
    
    #calc cumulative num obs
    cycle_obs = []
    for i, n in enumerate(cycles[:]):
        cycle_obs.append(total_obs//n)
    
    xilist = []
    xtlist = []
    target_radius_delta=0.3
    radius_range_offset = .3
    for co in cycle_obs:
        x_input_a,x_target_a = multi_radius_inputs_outputs2D(co, in_radius, target_radius_delta,radius_range_offset,step_offset, center)
        xilist.append(x_input_a)
        xtlist.append(x_target_a)
        
    xlist = []
    tlist = []
    for i, c in enumerate(cycles):
        xi = np.array(xilist[i])
        xt = np.array(xtlist[i])
        for ii in range(c-1):
            xi = np.concatenate([xi,xilist[i]],1)
            xt = np.concatenate([xt,xtlist[i]],1)
            
        ###################### xlist contains different shapes
        xlist.append(xi[:,loop_obs*skip_loops:,:])
        tlist.append(xt[:,loop_obs*skip_loops:,:])
    x_input = np.reshape(xlist,[len(cycles),-1,2])
    x_target = np.reshape(tlist,[len(cycles),-1,2])
    
    if len(cycles) ==1:
        #two harmonics
        return x_input[0], x_target[0]
    if len(cycles) ==2:
        #two harmonics
        x_input_a = np.concatenate([x_input[0],x_input[1]],1)
        x_target_a = np.concatenate([x_target[0],x_target[1]],1)
    elif len(cycles) ==3:      
        #three harmonics
        x_input_a = np.concatenate([x_input[0],x_input[1],x_input[2]],1)
        x_target_a = np.concatenate([x_target[0],x_target[1],x_target[2]],1)
    elif len(cycles) ==4:        
        #three harmonics
        x_input_a = np.concatenate([x_input[0],x_input[1],x_input[2],x_input[3]],1)
        x_target_a = np.concatenate([x_target[0],x_target[1],x_target[2],x_target[3]],1)
    else:
        print('unsupported number of cycles')
        
    return x_input_a, x_target_a

In [6]:
def set_random_seed(seed, deterministic=False):
    """Set random seed.

    Args:
        seed (int): Seed to be used.
        deterministic (bool): Whether to set the deterministic option for
            CUDNN backend, i.e., set `torch.backends.cudnn.deterministic`
            to True and `torch.backends.cudnn.benchmark` to False.
            Default: False.
    """
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)
    if deterministic:
        torch.backends.cudnn.deterministic = True
        torch.backends.cudnn.benchmark = False
        
def up_down_sample(list, new_size):
    '''
    take a list of data and resize the first dimension by building an idex of integers to sample
    if the new size is smaller it will add duplicates, no interpolation is taking place
    
    '''
    char_size = len(list)
    ind = char_size/new_size
    rng = np.arange(new_size, dtype='int32') #index range
    idx = np.array(np.floor(rng*ind), dtype='int32')

    return np.array(list)[idx]

def normalize_strokes(strokes):
    '''
    Center and size stroke xyz dimensions between 0 and 1 
    
    '''
    sa = []
    saa = []
    minX,minY,minZ,maxX,maxY,maxZ = 100,100,100,-100,-100,-100
    for s in strokes:
        minX = min(minX,np.min(s[:,:,0]))
        maxX = max(maxX,np.max(s[:,:,0]))
        minY = min(minY,np.min(s[:,:,1]))
        maxY = max(maxY,np.max(s[:,:,1]))       
        minZ = min(minZ,np.min(s[:,:,2]))
        maxZ = max(maxZ,np.max(s[:,:,2]))
        
    difx = maxX-minX
    dify = maxY-minY
    difz = maxZ-minZ    
    max_dim = max(difx,dify,difz)    
    mult = 1/max_dim
    
    #move min to 0 and scale to 1 for largest dimension
    for st in strokes:
        s = np.array(st)
        s[:,:,0] = s[:,:,0]-minX
        s[:,:,1] = s[:,:,1]-minY
        s[:,:,2] = s[:,:,2]-minZ
        s = s*mult
        sa.append(s)
    
    #recalculate max values and offset 1/2 the distance to 1 
    maxX,maxY,maxZ = -100,-100,-100
    for s in sa:
        maxX = max(maxX,np.max(s[:,:,0]))
        maxY = max(maxY,np.max(s[:,:,1]))       
        maxZ = max(maxZ,np.max(s[:,:,2]))        
        offsetX = (1-maxX)/2
        offsetY = (1-maxY)/2
        offsetZ = (1-maxZ)/2
        
    for st in sa:
        s = np.array(st)
        s[:,:,0] = s[:,:,0]+offsetX
        s[:,:,1] = s[:,:,1]+offsetY
        s[:,:,2] = s[:,:,2]+offsetZ
        saa.append(s)

    return saa


In [7]:


def graph_curves(xyCurves, layout=go.Layout(),labels=[], dashRange=range(0,0), mode='lines+markers'):
    traces = []
    for i in range (0, len(xyCurves)):
        xyCa = np.array(xyCurves[i])
        if i < len(labels):
            label = labels[i]
        else:
            label = str(i)
            
        #create a line/spline for each curve   
        sc = go.Scatter(
            x =  xyCa[0]
            ,y = xyCa[1]
            ,name = label
            ,line = dict(shape='spline')  
            )
        #add dash attributes if within dashRange
        sc.mode=mode
        if i in dashRange:
            sc.line['dash'] = '2px,6px'
            sc.marker['symbol'] = 'star'
            
        traces.append(sc)
    return go.Figure(data=traces, layout=layout)


def add_trace(subplot,trace,row,col):
    for d in trace.data:
        subplot.add_traces(d, rows=[row], cols=[col])
    return

def graph_quiver(x_input_a,pred,dims,name,scale=.8, arrow_scale=.3):
    xi = x_input_a[:,dims]
    xt = pred[:,dims]
    uv = xt-xi;
    x= xi[:,0];y= xi[:,1];u = uv[:,0];v = uv[:,1];
    qt = ff.create_quiver(x, y, u, v,
            scale=scale,
            arrow_scale=arrow_scale,
            name=name,
          )
    return qt



def x_unflatten(x,num_attractors,num_cycles):
    feature_size = x.shape[-1]
    return np.reshape(x,[num_attractors,num_cycles,-1,feature_size])

In [8]:
def graph_char(char_data, range=(0,-1),mode='lines', layout=layout):    
    (start,end) = range 
    if end < 0: end = char_data.shape[0]
    data = char_data[start:end]
    
    g = [
    [data[:,0],data[:,1]],
    [data[:,3],data[:,4]],
    [data[:,6],data[:,7]],
    
    [data[:,9],data[:,10]],
    [data[:,12],data[:,13]],
    [data[:,15],data[:,16]],
    
    [data[:,18],data[:,19]],
    [data[:,21],data[:,22]],
    [data[:,24],data[:,25]],
    
    [data[:,27],data[:,28]],
    [data[:,30],data[:,31]],
    [data[:,33],data[:,34]],    
    ]

    return graph_curves(g,layout=layout,mode=mode)

def graph_charZ(char_data, range=(0,-1),mode='lines'):    
    (start,end) = range    
    if end < 0: end = char_data.shape[0]
    data = char_data[start:end]
    g = [
    [data[:,2],data[:,1]],
    [data[:,5],data[:,4]],
    [data[:,8],data[:,7]],
    
    [data[:,11],data[:,10]],
    [data[:,14],data[:,13]],
    [data[:,17],data[:,16]],
    
    [data[:,20],data[:,19]],
    [data[:,23],data[:,22]],
    [data[:,26],data[:,25]],
    
    [data[:,29],data[:,28]],
    [data[:,32],data[:,31]],
    [data[:,35],data[:,34]],      
    ]

    return graph_curves(g,layout=layout,mode=mode)

### Data

In [9]:
def read_char(prefix='blend_out', char_num=0, target_char_obs=21):
    target_char_obs=21
    prefix='blend_out'

    path=CURRENT_MODEL_SAVE_DIR+prefix+'L'+ str(char_num) +'.json'
#     print(path)
    with open(path, 'r') as fp:
        jL = np.array(json.load(fp))
    path=CURRENT_MODEL_SAVE_DIR+prefix+'C'+ str(char_num) +'.json'
    with open(path, 'r') as fp:
        jC = np.array(json.load(fp))
    path=CURRENT_MODEL_SAVE_DIR+prefix+'R'+ str(char_num) +'.json'
    with open(path, 'r') as fp:
        jR = np.array(json.load(fp))
    path=CURRENT_MODEL_SAVE_DIR+prefix+'T'+ str(char_num) +'.json'
    with open(path, 'r') as fp:
        jT = np.array(json.load(fp))

    stroke_list = normalize_strokes([jL,jC,jR,jT,])    
    ud = [
        up_down_sample(stroke_list[0],target_char_obs),#stroke 0 of 4
        up_down_sample(stroke_list[1],target_char_obs),
        up_down_sample(stroke_list[2],target_char_obs),
        up_down_sample(stroke_list[3],target_char_obs),
    ]    
    ma = np.moveaxis(np.array(ud),[0,1], [1,0]) #move time to first dimension
    mac = np.array(ma) #clone
    ###
    num_obs = ma.shape[0]
    mf = np.reshape(ma, [num_obs,-1]) #reshape for training target
    mrab = np.reshape(mac, [num_obs,-1]) #reshape for training target
    mb = np.flip(mrab,0) #reverse time order
    ##
    a = np.linspace(0,1,num_obs)*math.pi
    a = np.cos(a)

    an = np.ones(mac[:,:,:,2].shape)
    mac[:,:,:,2] = mac[:,:,:,2]+an *.1

    num_obs = ma.shape[0]
    mf = np.reshape(ma, [num_obs,-1]) #reshape for training target
    mrab = np.reshape(mac, [num_obs,-1]) #reshape for training target
    mb = np.flip(mrab,0) #reverse time order
    char_flat_data = np.concatenate([mf, mb],0)
    return char_flat_data


In [10]:
'''


'''
fname = '2-hand 6-cycle attractor near-strange'
net_shape = [[4,40,20],[20,10,4]]
activation = Snake(2)
e_model = Model(input_size=4, hidden_size=40, output_size=20, activation=activation)
da_model = Model(input_size=20, hidden_size=10, output_size=4, activation=activation)

PATH = CURRENT_MODEL_SAVE_DIR + fname + '.cfg'
with open(PATH, 'r') as fp:
    parmsT = json.load(fp)
print(PATH, '\n',parmsT)

PATH = CURRENT_MODEL_SAVE_DIR + fname + 'E.pth'
with open(PATH, 'r') as fp:
    e_model.load_state_dict(torch.load(PATH))

PATH = CURRENT_MODEL_SAVE_DIR + fname + 'DA.pth'
with open(PATH, 'r') as fp:
    da_model.load_state_dict(torch.load(PATH))
    
a_model = Pair_Model(e_model,da_model)
for param in a_model.parameters():
    param.requires_grad = False
    
a_model

./save/2-hand 6-cycle attractor near-strange.cfg 
 {'loop_obs': 42, 'in_radius': [], 'cycle_counts': [1, 6], 'target_radius_delta': 0.3, 'radius_range_offset': 0.3, 'skip_loops': 0, 'step_offset': 1, 'center': 0.5, 'activation': 'Snake(2)', 'loss_fn': 'nn.SmoothL1Loss()', 'net_shape': [[4, 40, 20], [20, 10, 4]], 'hash': 4842783881822409549, 'fname': '2-hand 6-cycle attractor near-strange', 'save_time': 'November 19 2021 15:14'}


Pair_Model(
  (inputModel): Model(
    (activation): Snake()
    (rnn): RNN(
      (activation): Snake()
      (i2h0): Linear(in_features=44, out_features=40, bias=True)
      (h2o0): Linear(in_features=40, out_features=20, bias=True)
      (i2h1): Linear(in_features=60, out_features=40, bias=True)
      (h2o1): Linear(in_features=40, out_features=20, bias=True)
    )
    (fc): Linear(in_features=40, out_features=20, bias=True)
  )
  (outputModel): Model(
    (activation): Snake()
    (rnn): RNN(
      (activation): Snake()
      (i2h0): Linear(in_features=30, out_features=10, bias=True)
      (h2o0): Linear(in_features=10, out_features=4, bias=True)
      (i2h1): Linear(in_features=14, out_features=10, bias=True)
      (h2o1): Linear(in_features=10, out_features=4, bias=True)
    )
    (fc): Linear(in_features=10, out_features=4, bias=True)
  )
)

In [11]:
'''
strange attractor model

'''

fname = '2-hand 6-cycle attractor near-strange-e3200'
net_shape = [[4,40,20],[20,10,4]]
activation = Snake(2)
es_model = Model(input_size=4, hidden_size=40, output_size=20, activation=activation)
das_model = Model(input_size=20, hidden_size=10, output_size=4, activation=activation)

PATH = CURRENT_MODEL_SAVE_DIR + fname + '.cfg'
with open(PATH, 'r') as fp:
    parmsT = json.load(fp)
print(PATH, '\n',parmsT)

PATH = CURRENT_MODEL_SAVE_DIR + fname + 'E.pth'
with open(PATH, 'r') as fp:
    es_model.load_state_dict(torch.load(PATH))

PATH = CURRENT_MODEL_SAVE_DIR + fname + 'DA.pth'
with open(PATH, 'r') as fp:
    das_model.load_state_dict(torch.load(PATH))
    
as_model = Pair_Model(es_model,das_model)
for param in a_model.parameters():
    param.requires_grad = False
    
as_model

./save/2-hand 6-cycle attractor near-strange-e3200.cfg 
 {'loop_obs': 42, 'in_radius': [], 'cycle_counts': [1, 6], 'target_radius_delta': 0.3, 'radius_range_offset': 0.3, 'skip_loops': 0, 'step_offset': 1, 'center': 0.5, 'activation': 'Snake(2)', 'loss_fn': 'nn.SmoothL1Loss()', 'net_shape': [[4, 40, 20], [20, 10, 4]], 'hash': -1253669503920696458, 'fname': '2-hand 6-cycle attractor near-strange-e3200', 'save_time': 'November 20 2021 12:15'}


Pair_Model(
  (inputModel): Model(
    (activation): Snake()
    (rnn): RNN(
      (activation): Snake()
      (i2h0): Linear(in_features=44, out_features=40, bias=True)
      (h2o0): Linear(in_features=40, out_features=20, bias=True)
      (i2h1): Linear(in_features=60, out_features=40, bias=True)
      (h2o1): Linear(in_features=40, out_features=20, bias=True)
    )
    (fc): Linear(in_features=40, out_features=20, bias=True)
  )
  (outputModel): Model(
    (activation): Snake()
    (rnn): RNN(
      (activation): Snake()
      (i2h0): Linear(in_features=30, out_features=10, bias=True)
      (h2o0): Linear(in_features=10, out_features=4, bias=True)
      (i2h1): Linear(in_features=14, out_features=10, bias=True)
      (h2o1): Linear(in_features=10, out_features=4, bias=True)
    )
    (fc): Linear(in_features=10, out_features=4, bias=True)
  )
)

In [12]:
char_data_raw0 = read_char(prefix='blend_out', char_num=0, target_char_obs=21)
char_data_raw1 = read_char(prefix='blend_out', char_num=1, target_char_obs=21)
char_data_raw2 = read_char(prefix='blend_out', char_num=2, target_char_obs=21)

char_data_raw = np.concatenate([char_data_raw0,char_data_raw0,char_data_raw1,char_data_raw1,char_data_raw2,char_data_raw2],0)
# char_data_raw = np.concatenate([char_data_raw0,char_data_raw1,char_data_raw1,char_data_raw2,char_data_raw2,],0)

char_data_raw0.shape,char_data_raw.shape

((42, 36), (252, 36))

In [13]:
graph_char(char_data_raw2, range=(0,100),mode='lines')

In [14]:
graph_charZ(char_data_raw[:42, ], range=(0,100),mode='lines')

In [15]:
'''
skip_loops will cause a change in the requirements for the length of char input

'''

loop_obs = 42

parmsT = {
    'loop_obs':loop_obs,
    'in_radius':[],
    'cycle_counts':[1,6],
    'skip_loops':0,
    'step_offset':1,
    'center':0.5
    }
datasetT = Char_Dataset(char_data_raw, parmsT)

parmsL = copy.deepcopy(parmsT)
parmsL['in_radius'] = [.49,.51]
parmsL['skip_loops'] = 0
datasetL = Char_Dataset(char_data_raw,parmsL)

# datasetT.x_filter.shape, datasetT.char_filter.shape, datasetL.x_input.shape, datasetL.char_target.shape, parmsT
# datasetT.char_target.shape[0]/21, datasetL.char_target.shape[0]/21 #(20.0, 24.0)
# datasetT.x_input.shape[0]/21, datasetL.x_input.shape[0]/21         #(20.0, 20.0)
datasetT.char_filter.shape

torch.Size([504, 36])

In [16]:
ds = datasetT
# ds = datasetL

f,t = 42*0, 42*1000
xi = ds.x_input_a[f:t]
xt = ds.x_target_a[f:t]

pp_attractor = py.subplots.make_subplots(rows=1, cols=2,subplot_titles = [])
add_trace(pp_attractor,graph_quiver(xi,xt,[0,1],'.4',.6,.4),row=1,col=1)
add_trace(pp_attractor,graph_quiver(xi,xt,[0,3],'.4',.8,.1),row=1,col=2)

pp_attractor.layout.xaxis.range = [-.3,1.3]
pp_attractor.layout.yaxis.range = [-.3,1.3]

pp_attractor

In [17]:
xi = ds.x_input_a
xtt = ds.x_target_a
f,t = loop_obs*0, loop_obs*120000

gqi01 = graph_quiver(xi[f:t],xtt[f:t],[0,1],'gqi01',.99)
gqi23 = graph_quiver(xi[f:t],xtt[f:t],[2,3],'gqi23',.99)
gqi02 = graph_quiver(xi[f:t],xtt[f:t],[0,2],'gqi02',.99)
gqi03 = graph_quiver(xi[f:t],xtt[f:t],[0,3],'gqi03',.99)

# tl = [str(parms['in_radius']), str(parms['out_radius'])]
pp_attractor = py.subplots.make_subplots(rows=1, cols=4) #,subplot_titles = tl)                                                                        
add_trace(pp_attractor,gqi01,row=1,col=1)
add_trace(pp_attractor,gqi23,row=1,col=2)
add_trace(pp_attractor,gqi02,row=1,col=3)
add_trace(pp_attractor,gqi03,row=1,col=4)

####

pp_attractor.layout.xaxis.range = [-.2,1.2]
pp_attractor.layout.yaxis.range = [-.2,1.2]
pp_attractor.update_layout(template='simple_white',height=350, width=1000,showlegend=True, title=f'' )
pp_attractor

### Train

In [18]:
'''
datasetT.x_filter.shape, datasetT.char_filter.shape 

'''
############################################
train=False
device = 'cpu'
set_random_seed(43, deterministic=True)
print(f'{device=}, {train=}')

activation = Snake(2)
net_shape = [[4,40,20],[20,60,36]]
dg_model = Model(input_size=20, hidden_size=60, output_size=36, activation=activation)
dg_model.requires_grad_(True)
g_model = Pair_Model(e_model,dg_model)

parmsT['activation'] = 'Snake(2)'
parmsT['loss_fn'] = 'nn.SmoothL1Loss()'
parmsT['net_shape'] = net_shape
loss_fn = nn.SmoothL1Loss()
cnt = 0

# datasetT.x_filter.shape, datasetT.char_filter.shape 
g_model

device='cpu', train=False


Pair_Model(
  (inputModel): Model(
    (activation): Snake()
    (rnn): RNN(
      (activation): Snake()
      (i2h0): Linear(in_features=44, out_features=40, bias=True)
      (h2o0): Linear(in_features=40, out_features=20, bias=True)
      (i2h1): Linear(in_features=60, out_features=40, bias=True)
      (h2o1): Linear(in_features=40, out_features=20, bias=True)
    )
    (fc): Linear(in_features=40, out_features=20, bias=True)
  )
  (outputModel): Model(
    (activation): Snake()
    (rnn): RNN(
      (activation): Snake()
      (i2h0): Linear(in_features=80, out_features=60, bias=True)
      (h2o0): Linear(in_features=60, out_features=36, bias=True)
      (i2h1): Linear(in_features=96, out_features=60, bias=True)
      (h2o1): Linear(in_features=60, out_features=36, bias=True)
    )
    (fc): Linear(in_features=60, out_features=36, bias=True)
  )
)

In [19]:
# '''
# training loop

# '''
parmsT['net_shape'] = net_shape

# epochs = 10
epochs = 1000
# epochs = 10000

# lr = .005
lr=0.003
lr=0.001
lr=0.0001
lr=0.00001
# lr=0.000001

optimizer = torch.optim.Adam(g_model.parameters(), lr=lr)
if train:
    min_loss = 1000
    max_loss = 0
    start = time.time()
    for epoch in range(epochs):
        optimizer.zero_grad() # Clears existing gradients from previous epoch
        datasetT = Char_Dataset(char_data_raw,parmsT)
        output, hidden = g_model(datasetT.x_filter)
        target = datasetT.char_filter.to(device)

        loss = loss_fn(output, target) # loss = criterion(output, target_seq.view(-1).long())
        if loss < min_loss: min_loss = loss
        if loss > max_loss: max_loss = loss

        loss.backward() # Do backpropagation and calculates gradients
        optimizer.step() # Updates the weights accordingly
        if epoch % (epochs/10) == 0:
            loss = loss_fn(output, target)
            print(f'{cnt=}, {loss.data:.7f}')
        cnt+=1

    print(parmsT)
    print(f'epochs={cnt}, loss={loss.data*100000:.4f}, min loss={min_loss.data*100000:.4f}, max loss={max_loss.data*100000:.2f}, {lr=}')
    print('\ntime: {0:.2f}'.format( time.time()-start))
else:
    fname = '2-hand 6-cycle attractor char pair loop'
    PATH = CURRENT_MODEL_SAVE_DIR + fname + '.cfg'
    print(PATH)
    with open(PATH, 'r') as fp:
        parmsT = json.load(fp)
    print(parmsT)
    
    dg_model = Model(input_size=20, hidden_size=60, output_size=36, activation=activation)
#     fname = '2-hand 6-cycle attractor char pair'
    PATH = CURRENT_MODEL_SAVE_DIR + fname + 'dg.pth'
    print(PATH)
    dg_model.load_state_dict(torch.load(PATH))
    g_model = Pair_Model(e_model,dg_model)


./save/2-hand 6-cycle attractor char pair loop.cfg
{'loop_obs': 42, 'in_radius': [], 'cycle_counts': [1, 6], 'target_radius_delta': 0.3, 'radius_range_offset': 0.3, 'skip_loops': 0, 'step_offset': 1, 'center': 0.5, 'activation': 'Snake()', 'loss_fn': 'SmoothL1Loss()', 'net_shape': [[4, 40, 20], [20, 10, 4]], 'hash': -4865353530312562613, 'fname': '2-hand 6-cycle attractor char pair loop', 'save_time': 'December 05 2021 14:18', 'shape': [[4, 40, 20], [20, 10, 4]]}
./save/2-hand 6-cycle attractor char pair loopdg.pth


In [20]:
'''
{'loop_obs': 42, 'in_radius': [], 'cycle_counts': [1, 6], 'skip_loops': 0, 'step_offset': 1, 'center': 0.5, 'net_shape': [[4, 40, 20], [20, 60, 36]], 'hash': 1399900535305257313, 'fname': '2-hand 6-cycle attractor char pair loop', 'shape': [[4, 40, 20], [20, 50, 36]], 'loss_fn': 'nn.SmoothL1Loss()', 'activation': 'Snake(2)', 'save_time': 'November 21 2021 12:02'}
epochs=1000, loss=14.9206, min loss=14.4078, max loss=16485.63, lr=0.003
epochs=2000, loss=7.0705, min loss=6.4877, max loss=172.76, lr=0.001
epochs=3000, loss=5.7406, min loss=4.7000, max loss=266.87, lr=0.001
epochs=4000, loss=4.6835, min loss=4.4041, max loss=7.50, lr=1e-05

{'loop_obs': 42, 'in_radius': [], 'cycle_counts': [1, 6], 'skip_loops': 0, 'step_offset': 1, 'center': 0.5, 'net_shape': [[4, 40, 20], [20, 60, 36]], 'hash': 1399900535305257313, 'fname': '2-hand 6-cycle attractor char pair loop', 'shape': [[4, 40, 20], [20, 50, 36]], 'loss_fn': 'nn.SmoothL1Loss()', 'activation': 'Snake(2)', 'save_time': 'November 21 2021 12:02'}
epochs=1000, loss=46.7363, min loss=42.1214, max loss=16485.63, lr=0.001
epochs=2000, loss=12.4028, min loss=11.1306, max loss=258.87, lr=0.001
epochs=3000, loss=9.0838, min loss=7.1630, max loss=432.01, lr=0.001
epochs=4000, loss=6.3510, min loss=6.0525, max loss=12.25, lr=0.0001
epochs=5000, loss=5.9219, min loss=5.4123, max loss=10.40, lr=0.0001
epochs=6000, loss=8.3420, min loss=5.2388, max loss=9.65, lr=1e-05
epochs=7000, loss=9.3757, min loss=5.2374, max loss=9.52, lr=1e-06

{'loop_obs': 42, 'in_radius': [], 'cycle_counts': [1, 6], 'skip_loops': 0, 'step_offset': 1, 'center': 0.5, 'activation': 'Snake(2)', 'loss_fn': 'nn.SmoothL1Loss()', 'net_shape': [[4, 40, 20], [20, 50, 36]]}
epochs=1000, loss=22.0779, min loss=20.4670, max loss=18849.13, lr=0.003
epochs=2000, loss=10.2714, min loss=9.3843, max loss=282.72, lr=0.001
epochs=3000, loss=9.9783, min loss=7.7372, max loss=15.96, lr=0.0001
epochs=4000, loss=7.1946, min loss=6.7860, max loss=13.56, lr=0.0001
epochs=5000, loss=7.1423, min loss=6.5542, max loss=11.64, lr=1e-05
epochs=6000, loss=10.0370, min loss=6.4179, max loss=11.56, lr=1e-05
epochs=7000, loss=11.2646, min loss=6.4121, max loss=11.42, lr=1e-06

epochs=1000, loss=12.0322, min loss=7.5227, max loss=18277.89, lr=0.003
epochs=2000, loss=3.7592, min loss=3.7417, max loss=221.57, lr=0.001
epochs=3000, loss=2.9701, min loss=2.8157, max loss=202.42, lr=0.001
epochs=4000, loss=2.3811, min loss=2.3811, max loss=4.94, lr=0.0001

'''
pass

### Evaluate

In [21]:
'''


'''
parmsE = copy.deepcopy(parmsT)
# parmsE['in_radius'] = [.25, .40, 0.48, 0.51, .61]
parmsE['in_radius'] = [.5]
parmsE['skip_loops'] = 0
datasetE = Char_Dataset(char_data_raw,parmsE)

input_dims = datasetE.x_input.shape[1]
xe_input_a = datasetE.x_input_a
xe_hat, _ = a_model(datasetE.x_input)
xe_hat_a = xe_hat.detach().numpy()


In [22]:
'''
recursive path through attractor (output -> input)
alternative attractor models can be used to explore variations

'''

rrange = 10000
r_model = as_model
# r_model = a_model

r_input = datasetL.x_input[0]+torch.ones([input_dims],dtype=torch.float)*-0.
r_outL = [r_input.detach().numpy()] #start point
r_input = r_input.unsqueeze(0)
for i in range(rrange-1):
    r_out, _ = r_model(r_input)
    r_outL.append(r_out[0].detach().numpy())
    r_input = r_out
r_outA = np.array(r_outL)

r_outA.shape

(10000, 4)

#### X Out

In [23]:
'''
Attractor periodicity based on tolerance

'''
inperiod = False
inpoint = False
inattract = False
lastperiodi = 999
minn= 1000

tolerance = .00159

print(r_outA[-1])
for i in range(r_outA.shape[0]):
    dif = r_outA[-1] - r_outA[i]
    sq = np.square(dif)
    maxx = np.max(sq)
    if maxx < minn: 
        minn = maxx
    if maxx < tolerance:
        inattract = True
        if lastperiodi == 999: 
            print(i,f'{inattract=}, for tolerance {tolerance}')
            lastperiodi = i
        print(i,f'period: {i-lastperiodi}/{round((i-lastperiodi)/21)}')
        lastperiodi = i
    if (inattract == True) and np.max(np.square(r_outA[i]-r_outA[i-5])) < tolerance:
        print(i, 'in point attractor','\n',r_outA[i])
        break
    if (inattract == True) and maxx>minn:
        inperiod = True


[0.82979 0.14724 0.41375 1.06926]
592 inattract=True, for tolerance 0.00159
592 period: 0/0
846 period: 254/12
1100 period: 254/12
2076 period: 976/46
2329 period: 253/12
2583 period: 254/12
3559 period: 976/46
3812 period: 253/12
4066 period: 254/12
5042 period: 976/46
5295 period: 253/12
5549 period: 254/12
6525 period: 976/46
6778 period: 253/12
7032 period: 254/12
8262 period: 1230/59
8516 period: 254/12
9745 period: 1229/59
9999 period: 254/12


In [24]:
'''
[0.82979 0.14724 0.41375 1.06926]
846 inattract=True, for tolerance 0.00055
846 period: 0/0
8262 period: 7416/353
9999 period: 1737/83

[0.82979 0.14724 0.41375 1.06926]
846 inattract=True, for tolerance 0.0006
846 period: 0/0
1100 period: 254/12
8262 period: 7162/341
9999 period: 1737/83

[0.82979 0.14724 0.41375 1.06926]
846 inattract=True, for tolerance 0.0008
846 period: 0/0
1100 period: 254/12
2583 period: 1483/71
5549 period: 2966/141
8262 period: 2713/129
9745 period: 1483/71
9999 period: 254/12

[0.82979 0.14724 0.41375 1.06926]
846 inattract=True, for tolerance 0.001
846 period: 0/0
#1100 period: 254/12
2076 period: 976/46
#2583 period: 507/24
3559 period: 976/46
4066 period: 507/24
#5549 period: 1483/71
7032 period: 1483/71
#8262 period: 1230/59
#9745 period: 1483/71
#9999 period: 254/12

[0.82979 0.14724 0.41375 1.06926]
592 inattract=True, for tolerance 0.00159
592 period: 0/0
846 period: 254/12
1100 period: 254/12
2076 period: 976/46
2329 period: 253/12
2583 period: 254/12
3559 period: 976/46
3812 period: 253/12
4066 period: 254/12
5042 period: 976/46
5295 period: 253/12
5549 period: 254/12
6525 period: 976/46
6778 period: 253/12
7032 period: 254/12
8262 period: 1230/59
8516 period: 254/12
9745 period: 1229/59
9999 period: 254/12

'''
pass

In [25]:
f,t = loop_obs*0, loop_obs*180
ri = r_outA[:-1]
rt = r_outA[1:]

layout3D = go.Layout(
     width = 600,
     height = 600,
     title = '',
     showlegend=True,
    scene = dict(
        xaxis = dict(nticks=4, range=[-.3,1.3]),
        yaxis = dict(nticks=4, range=[-.3,1.3],),
        zaxis = dict(nticks=4, range=[-.3,1.3],),
    ))

f3d = go.Scatter3d(x=rt[f:,0], y=rt[f:,1], z=rt[f:,3], mode='lines', marker=dict(symbol='circle', size=2))
ff3d = go.Figure(data=[f3d])
camera = dict(
#     eye=dict(x=1, y=-1, z=1.))
    eye=dict(x=.06, y=-.06, z=-1.7))

ff3d.update_layout(scene_camera=camera)
ff3d

In [85]:
'''
Calculate evaluation data
Two attractors

'''
xe_hat, _ = a_model(datasetL.x_input)
xe_hat_a = xe_hat.detach().numpy()
xi = datasetL.x_input.detach().numpy()
xtt = xe_hat_a

dims = [0,1]
dims = [0,3]
gq = graph_quiver(xi[:],xtt[:],dims,'gqi01',.4,.6)
gq.layout = layout
gq

In [27]:
xe_input_a = datasetL.x_input_a
input_dims = xe_input_a.shape[1]
xeuf_input_a = x_unflatten(xe_input_a,num_attractors=2,num_cycles=6) 

xe_hat, _ = a_model(datasetL.x_input)
xe_hat_a = xe_hat.detach().numpy()

xe_hat_a = xe_hat.detach().numpy()
xeuf_hat_a = x_unflatten(xe_hat_a,num_attractors=2,num_cycles=6) 

f,t = loop_obs*0, loop_obs*6
xi = np.reshape(xeuf_input_a[:,:,f:t],[-1,input_dims])
xtt = np.reshape(xeuf_hat_a[:,:,f:t],[-1,input_dims])
ri = r_outA[:-1]
rt = r_outA[1:]

gqi01 = graph_quiver(xi[f:t],xtt[f:t],[0,1],'gqi01',.99)
gqi23 = graph_quiver(xi[f:t],xtt[f:t],[2,3],'gqi23',.99)
gqi12 = graph_quiver(xi[f:t],xtt[f:t],[1,2],'gqi45',.99)

###
f,t = loop_obs*0, loop_obs*50
gqr01 = graph_quiver(ri[f:t],rt[f:t],[0,1],'gqr01',.99,.1)
gqr23 = graph_quiver(ri[f:t],rt[f:t],[2,3],'gqr23',.99,.1)
gqr12 = graph_quiver(ri[f:t],rt[f:t],[1,2],'gqr12',.99,.1)

##
tl = [str(parmsT['in_radius'])]
pp_attractor = py.subplots.make_subplots(rows=2, cols=4,subplot_titles = tl)                                                                        
add_trace(pp_attractor,gqi01,row=1,col=1)
add_trace(pp_attractor,gqi23,row=1,col=2)
add_trace(pp_attractor,gqi12,row=1,col=3)

add_trace(pp_attractor,gqr01,row=2,col=1)
add_trace(pp_attractor,gqr23,row=2,col=2)
add_trace(pp_attractor,gqr12,row=2,col=3)

pp_attractor.layout.xaxis.range = [-.1,1.1]
pp_attractor.layout.yaxis.range = [-.1,1.1]
pp_attractor.update_layout(template='simple_white',height=800, width=1200,showlegend=True, title=f'{net_shape=}, {lr=}, {cnt=}' )
pp_attractor

#### Char Out

In [28]:
'''
Target Characters

'''

# gm0, _ = g_model(datasetE.x_input)
# gm0, _ = g_model(datasetL.x_input)
gm0 = datasetL.char_filter
# gm0,_ = g_model(torch.tensor(r_outA))

gm0 = gm0.detach().numpy()
pp_char0 = py.subplots.make_subplots(rows=1, cols=3,shared_xaxes=True, shared_yaxes=True,
                    vertical_spacing=0.02) #,subplot_titles = tl)
fff=2
f=fff*21+0
t =f+42*1
print(fff,f,t)
add_trace(pp_char0,graph_char(gm0[f:t]),row=1,col=1)

fff=5
f=fff*21
t =f+42
print(fff,f,t)
add_trace(pp_char0,graph_char(gm0[f:t]),row=1,col=2)

fff=9
f=fff*21
t =f+42
print(fff,f,t)
add_trace(pp_char0,graph_char(gm0[f:t],),row=1,col=3)

pp_char0.update_layout(template='plotly_white',height=400, width=800) #height=800, width=600, 
pp_char0


2 42 84
5 105 147
9 189 231


In [29]:
'''
Graph forward and backward pass of the mesh, as well as average of forward and backward pass

'''

# gm1, _ = g_model(datasetE.x_input)
gm1, _ = g_model(datasetL.x_input)
# gm1,_ = g_model(torch.tensor(r_outA))

gm1 = gm1.detach().numpy()

f,t = 294,314
f,t = 3,23

gmF = gm1[f:t]
gmB1 = gm1[(f+21):(t+21)]
gmB = np.flip(gmB1,0)
gmA = np.average([gmF,gmB],0)
f,t, gmF.shape, gmB1.shape, gmB.shape, gmA.shape
pp_char0 = py.subplots.make_subplots(rows=1, cols=3,shared_xaxes=True, shared_yaxes=True,
                                 vertical_spacing=0.02)#,subplot_titles = tl)                                                                        
add_trace(pp_char0,graph_char(gmF),row=1,col=1)
add_trace(pp_char0,graph_char(gmB),row=1,col=2)
add_trace(pp_char0,graph_char(gmA),row=1,col=3)

pp_char0.update_layout(template='plotly_white',height=400, width=800) #height=800, width=600, 
pp_char0

In [79]:
'''
Explore different parts of the attractor

846 period: 254/12
1100 period: 254/12
2076 period: 976/46
2329 period: 253/12
2583 period: 254/12
3559 period: 976/46
3812 period: 253/12
4066 period: 254/12
5042 period: 976/46
5295 period: 253/12
5549 period: 254/12
6525 period: 976/46
6778 period: 253/12
7032 period: 254/12
8262 period: 1230/59
8516 period: 254/12
9745 period: 1229/59
9999 period: 254/12

'''
pp_char2 = py.subplots.make_subplots(rows=3, cols=3,subplot_titles = [])
pp_char2.layout.title = 'Example 2D char projections'
pp_char2.layout.height=1000
pp_char2.layout.width=800
pp_char2.layout.showlegend=False

predC, _ = g_model(torch.tensor(r_outA[:]))
predC = predC.detach().numpy()

# ss = 0+1 #1
# ss = 192+1 #2 3
# ss = 381+3 #2
ss = 573+6 #20
ss = 761+5 #5 8
ss = 3559+3 #3
ss = 3559+8 #20
ss = 8516+3 #3, #4, #5
ss = 9745+3 #7, #4, #6
d = 21
s = ss
for i in range(1,4):
    add_trace(pp_char2,graph_char(predC, range=(s,s+d)),  row=i,col=1)
    add_trace(pp_char2,graph_char(predC, range=(s+d,s+d*2)),  row=i,col=2)
    add_trace(pp_char2,graph_char(predC, range=(s+d*2,s+d*3)),  row=i,col=3)
    print((s,s+d),(s+d,s+d*2),(s+d*2,s+d*3))
#     print(s+d,s+d*2)
    s += d*3

# print(ss,s)
pp_char2

(9748, 9769) (9769, 9790) (9790, 9811)
(9811, 9832) (9832, 9853) (9853, 9874)
(9874, 9895) (9895, 9916) (9916, 9937)


In [83]:
'''
Gallery of different shapes

'''

pp_char3 = py.subplots.make_subplots(rows=4, cols=3,subplot_titles = [], horizontal_spacing = 0.05, vertical_spacing = 0.02)
pp_char3.layout.title = 'Example 2D char projections'
pp_char3.layout.height=1300
pp_char3.layout.width=1000
pp_char3.layout.showlegend=False

#target
add_trace(pp_char3,graph_char(gm0[42:84]),  row=1,col=1)
add_trace(pp_char3,graph_char(gm0[105:147]),  row=1,col=2)
add_trace(pp_char3,graph_char(gm0[189:231]),  row=1,col=3)

#iterative path into attractor
add_trace(pp_char3,graph_char(predC, range=(1,23)),  row=2,col=1)
add_trace(pp_char3,graph_char(predC, range=(193,212)),  row=2,col=2)
add_trace(pp_char3,graph_char(predC, range=(214, 235)),  row=2,col=3)

# add_trace(pp_char3,graph_char(predC, range=(235, 256)),  row=3,col=1)
add_trace(pp_char3,graph_char(predC, range=(234, 253)),  row=3,col=1)
add_trace(pp_char3,graph_char(predC, range=(572, 593)),  row=3,col=2)
# add_trace(pp_char3,graph_char(predC, range=(572, 590)),  row=3,col=2)
add_trace(pp_char3,graph_char(predC, range=(850, 871)),  row=3,col=3)

add_trace(pp_char3,graph_char(predC, range=(913, 932)),  row=4,col=1)
add_trace(pp_char3,graph_char(predC, range=(3604, 3625)),  row=4,col=2)
add_trace(pp_char3,graph_char(predC, range=(8645, 8666)),  row=4,col=3)

#(8645, 8666)
pp_char3

### Save

In [32]:
%%javascript
IPython.notebook.kernel.execute(`notebookName = '${window.document.getElementById("notebook_name").innerHTML}'`);

<IPython.core.display.Javascript object>

In [33]:
# fname = notebookName

# hash0 = hash(str(parmsT))
# parmsT['hash'] = hash0
# parmsT['fname'] = fname
# # parmsT['shape'] =  net_shape
# parmsT['loss_fn'] =  'SmoothL1Loss()'
# parmsT['activation'] =  'Snake()'
# parmsT['save_time'] = time.strftime("%B %d %Y %H:%M", time.localtime())

# PATH = CURRENT_MODEL_SAVE_DIR + fname + '.cfg'
# with open(PATH,'w') as f:
#     json.dump(parmsT,f)

# PATH = "./image/char2D-" + str(hash0) + ".png"
# pp_attractor.write_image(PATH)

# # PATH = "./image/char2D-" + str(hash0) + ".png"
# # pp_char0.write_image(PATH)

# # PATH = "./image/charloops-" + str(hash0) + ".png"
# # pp_char1.write_image(PATH)

# PATH = CURRENT_MODEL_SAVE_DIR + fname + 'dg.pth'
# torch.save(dg_model.state_dict(), PATH)

# PATH, parmsT

In [34]:
'''
('./save/2-hand 6-cycle attractor char pair loopdg.pth',
 {'loop_obs': 42,
  'in_radius': [],
  'cycle_counts': [1, 6],
  'target_radius_delta': 0.3,
  'radius_range_offset': 0.3,
  'skip_loops': 0,
  'step_offset': 1,
  'center': 0.5,
  'activation': 'Snake()',
  'loss_fn': 'SmoothL1Loss()',
  'net_shape': [[4, 40, 20], [20, 10, 4]],
  'hash': -4865353530312562613,
  'fname': '2-hand 6-cycle attractor char pair loop',
  'save_time': 'December 05 2021 14:18',
  'shape': [[4, 40, 20], [20, 10, 4]]})
'''
pass